

<table width="100%" style="padding:0; margin-left:-6px;">
    <tr style="padding=0;" width="100%">
        <td width="auto">
           <hr style="border:2px solid darkblue">
            <h1> nb1. Query one source</h1>
           <hr style="border:2px solid darkblue">
        </td>
        <td width="60px">
           <img src="ALMAsmall.png" align="right"/> 
        </td>
    </tr>
</table>    
        

In this notebook we query one source in three modes: 
    
* By coordinate:
    * within a certain radius around a given coordinate (for point sources) 
    * within a certain radius around a given coordinate, estimating the distance to the archival sources
<br/><br/>
* By the resolved source name using [Sesame](http://cds.u-strasbg.fr/cgi-bin/Sesame)
<br/><br/>
    
* By the ALMA source name
    * full name   
    * part of the name
    <br/><br/>
    
-------------

The relevant columns in the [ALMA Science Archive TAP service](https://almascience.org/tap) are 
* *s_ra*, *s_dec* (RA and Dec in degrees)
* *s_region* (STC-S footprint of the observation)
* *target_name* (source name)
 
--------- ----- -----


First we need to set up the python modules

In [1]:
import numpy as np
import astropy
import astropy.coordinates
import pyvo
import pandas as pd

service = pyvo.dal.TAPService("https://almascience.eso.org/tap")      # for the EU ALMA TAP service

# service = pyvo.dal.TAPService("https://almascience.nao.ac.jp/tap")  # for the EA ALMA TAP service
# service = pyvo.dal.TAPService("https://almascience.nrao.edu/tap")   # for the NA ALMA TAP service

<hr style="border:2px solid darkblue"> </hr>

## By coordinate

<hr style="border:2px solid darkblue"> </hr>



The most basic search of a source is based on its coordinates. To do this we use the INTERSECT function to find all observations where the footprint (s_region) overlaps with the search circle. 

In [2]:
def query_coordinate(service, ra, dec, radius):
    """Queries ALMA footprints that intersect the search circle
    
       service        pyvo TAPService instance           
       ra             Right Ascension in decimal degrees
       dec            Declination in decimal degrees
       radius         Search radius in decimal degrees
           
       returns        pandas table
       """    
    
    query = f"""
            SELECT * 
            FROM ivoa.obscore   
            WHERE INTERSECTS(CIRCLE('ICRS',{ra},{dec},{radius}),s_region)=1  """
    
    return service.search(query).to_table().to_pandas()

<hr style="border:2px solid darkblue"> </hr>

## By coordinate: Display and sort by distance

<hr style="border:2px solid darkblue"> </hr>




It is also possible to add a column to the ADQL output. For example we can now display the distance of the positions in the archive catalogue to the searched coordinate and sort by it.

In [3]:
def query_coordinate_display_distance(service, ra, dec, radius):
    """Queries ALMA footprints that intersect the search circle
    
       service        pyvo TAPService instance           
       ra             Right Ascension in decimal degrees
       dec            Declination in decimal degrees
       radius         Search radius in decimal degrees
           
       returns        pandas table including the distance column
       """    

    query = f""" 
            SELECT DISTANCE(POINT('ICRS', s_ra, s_dec), POINT('ICRS',{ra},{dec})) AS dist, * 
            FROM ivoa.obscore 
            WHERE INTERSECTS(CIRCLE('ICRS',{ra},{dec},{radius}),s_region)=1 
            ORDER BY dist"""

    return service.search(query).to_table().to_pandas()

<hr style="border:2px solid darkblue"> </hr>

## By the resolved source name

<hr style="border:2px solid darkblue"> </hr>

Astropy comes with functionality to resolve astronomical source names into coordinates using the [Sesame](http://cds.u-strasbg.fr/cgi-bin/Sesame) service of [CDS](http://cds.u-strasbg.fr). This can be combined with the coordinate query above.

In [4]:
coordinates = astropy.coordinates.SkyCoord.from_name("Cen A")
print(coordinates.ra.degree, coordinates.dec.degree)

201.36506288 -43.01911267


<hr style="border:2px solid darkblue"> </hr>

## By the ALMA source name
<hr style="border:2px solid darkblue"> </hr>

These two functions encapsulate the search for a source name **as given by the PI in the proposal to ALMA** (for a search using a name-resolver, see above):

In [5]:
def query_alma_source_name_exact(service, source_name):
    """ queries the ALMA source name as given by the PI
    
       service        pyvo TAPService instance           
       source_name    complete source name 
           
       returns        pandas table
    """
    
    query = f"""  
            SELECT *  
            FROM ivoa.obscore  
            WHERE target_name = '{source_name}' """
    
    return service.search(query).to_table().to_pandas()


def query_alma_source_name_included(service, source_name):
    """ queries a portion of the ALMA source name as given by the PI
    
       service        pyvo TAPService instance           
       source_name    portion of the source name 
           
       returns        pandas table
    """   
    
    query = f""" 
            SELECT *  
            FROM ivoa.obscore  
            WHERE target_name LIKE '%{source_name}%'  """
    
    return service.search(query).to_table().to_pandas()

-----------------

## Example 1a: Find sources at coordinate RA: 201.365, DEC: -43.019

In [6]:
results = query_coordinate(service, 201.365, -43.019, 0.006)
results.head(5)

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

       proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00008.SV      Public     309.512363     19.416239   
1  2011.0.00008.SV      Public     309.512363     19.416239   
2  2011.0.00008.SV      Public     309.512363     19.416239   
3  2011.0.00008.SV      Public     309.512363     19.416239   
4   2011.0.00010.S      Public     309.515914     19.417224   

              obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
4   ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   

   ...   frequency velocity_resolution   obs_creator_name  \
0  ...  238.261613         1183.847494  observatory, ALMA   
1  ...  238.261613         1183.847494  observatory, ALMA   
2  ...  238.261613         1183.847494  observatory, ALMA   
3  ...  238.261613         1183.847494  observatory, ALMA   
4  ...  219.025328          663.940713       Ott, Juergen   

                                           pub_title  \
0  ALMA Observations of the Physical and Chemical...   
1  ALMA Observations of the Physical and Chemical...   
2  ALMA Observations of the Physical and Chemical...   
3  ALMA Observations of the Physical and Chemical...   
4  ALMA Observations of the Physical and Chemical...   

                                 first_author  qa2_passed  \
0  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
1  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
2  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
3  Azeez, Jazeel H. Israel, F. P. McCoy, Mark           T   
4                                 McCoy, Mark           T   

                                       bib_reference  \
0  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
1  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
2  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
3  2014A&A...562A..96I 2017AdAst2017E...6A 2017Ap...   
4                                2017ApJ...851...76M   

                                     science_keyword  scientific_category  \
0  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
1  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
2  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
3  Galactic centres/nuclei, Active Galactic Nucle...      Active galaxies   
4  Active Galactic Nuclei (AGN)/Quasars (QSO), Me...      Active galaxies   

              lastModified  
0  2021-09-30T16:34:41.133  
1  2021-09-30T16:34:41.133  
2  2021-09-30T16:34:41.133  
3  2021-09-30T16:34:41.133  
4  2021-09-30T16:34:41.133  

[5 rows x 63 columns]

The same query but now adding the distance column:

In [7]:
pd.set_option('display.max_columns', None)

results = query_coordinate_display_distance(service, 201.365, -43.019, 0.006)
results.head(5)

dist                                         access_url access_format  \
0  1.484554  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  1.484554  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  1.484554  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  5.772087  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  5.772087  http://almascience.org/aq?member_ous_id=uid://...     text/html   

      proposal_id data_rights  gal_longitude  gal_latitude  \
0  2012.1.00225.S      Public     309.515896     19.417338   
1  2012.1.00225.S      Public     309.515896     19.417338   
2  2012.1.00225.S      Public     309.515896     19.417338   
3  2012.1.00225.S      Public     309.515937     19.417346   
4  2012.1.00225.S      Public     309.515937     19.417346   

             obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2012.1.00225.S           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2012.1.00225.S           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2012.1.00225.S           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2012.1.00225.S           ALMA           JAO            ALMA   
4  ADS/JAO.ALMA#2012.1.00225.S           ALMA           JAO            ALMA   

                   obs_id dataproduct_type  calib_level  target_name  \
0  uid://A002/X7d1738/X58             cube            2  Centaurus_a   
1  uid://A002/X7d1738/X58             cube            2  Centaurus_a   
2  uid://A002/X7d1738/X58             cube            2  Centaurus_a   
3  uid://A002/X7d1738/Xf8             cube            2  Centaurus_a   
4  uid://A002/X7d1738/Xf8             cube            2  Centaurus_a   

         s_ra      s_dec     s_fov  \
0  201.365018 -43.019002  0.018076   
1  201.365018 -43.019002  0.018076   
2  201.365018 -43.019002  0.018076   
3  201.365069 -43.018989  0.009992   
4  201.365069 -43.018989  0.009992   

                                            s_region  s_resolution  \
0         Circle ICRS 201.365018 -43.019002 0.009038      1.170768   
1         Circle ICRS 201.365018 -43.019002 0.009038      1.170768   
2         Circle ICRS 201.365018 -43.019002 0.009038      1.170768   
3  Polygon ICRS 201.368089 -43.022662 201.367662 ...      0.165660   
4  Polygon ICRS 201.368089 -43.022662 201.367662 ...      0.165660   

          t_min         t_max  t_exptime  t_resolution    em_min    em_max  \
0  56815.888687  56815.901698    211.680       211.680  0.003338  0.003374   
1  56815.888687  56815.901698    211.680       211.680  0.003371  0.003407   
2  56815.888687  56815.901698    211.680       211.680  0.003296  0.003330   
3  56761.195098  56761.420462    462.729       462.729  0.000434  0.000435   
4  56761.195098  56761.420462    462.729       462.729  0.000425  0.000426   

    em_res_power pol_states                                o_ucd band_list  \
0  183907.921659    /XX/YY/  phot.flux.density;phys.polarization         3   
1  182136.313740    /XX/YY/  phot.flux.density;phys.polarization         3   
2  186289.975282    /XX/YY/  phot.flux.density;phys.polarization         3   
3  707749.592794    /XX/YY/  phot.flux.density;phys.polarization         9   
4  721784.342900    /XX/YY/  phot.flux.density;phys.polarization         9   

   em_resolution                                            authors  \
0     613.938003  Espada, D.; Matsushita, S.; Miura, R. E.; Isra...   
1     613.938003  Espada, D.; Matsushita, S.; Miura, R. E.; Isra...   
2     613.938003  Espada, D.; Matsushita, S.; Miura, R. E.; Isra...   
3     306.991286  Espada, D.; Matsushita, S.; Miura, R. E.; Isra...   
4     306.991286  Espada, D.; Matsushita, S.; Miura, R. E.; Isra...   

                                        pub_abstract  publication_year  \
0  Previous investigations have employed more tha...              2016   
1  Previous investigations have employed more tha...              2016   
2  Previ

-----------------

## Example 1b: Query the source Centaurus A using Sesame

Many sources have a number of names and you can not be sure that the source name the PI placed into the ALMA proposal is the source name you have in mind. We use the name-resolver [Sesame](http://cds.u-strasbg.fr/cgi-bin/Sesame) provided by [CDS](http://cds.u-strasbg.fr) to first resolve the source name into coordinates and then search around those coordinates.

In [8]:
coordinates = astropy.coordinates.SkyCoord.from_name("Cen A")

In [9]:
query_coordinate(service, coordinates.ra.degree, coordinates.dec.degree, 0.006).head(5)

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

       proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00008.SV      Public     309.512363     19.416239   
1  2011.0.00008.SV      Public     309.512363     19.416239   
2  2011.0.00008.SV      Public     309.512363     19.416239   
3  2011.0.00008.SV      Public     309.512363     19.416239   
4   2011.0.00010.S      Public     309.515914     19.417224   

              obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
4   ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   

                    obs_id dataproduct_type  calib_level  target_name  \
0  uid://A002/X259150/X157             cube            2  Centaurus A   
1  uid://A002/X259150/X157             cube            2  Centaurus A   
2  uid://A002/X259150/X157             cube            2  Centaurus A   
3  uid://A002/X259150/X157             cube            2  Centaurus A   
4  uid://A002/X327408/X217             cube            2         CenA   

         s_ra      s_dec     s_fov  \
0  201.360719 -43.020553  0.058089   
1  201.360719 -43.020553  0.058089   
2  201.360719 -43.020553  0.058089   
3  201.360719 -43.020553  0.058089   
4  201.365063 -43.019112  0.007385   

                                            s_region  s_resolution  \
0  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
1  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
2  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
3  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
4         Circle ICRS 201.365063 -43.019112 0.003692      1.330912   

          t_min         t_max  t_exptime  t_resolution    em_min    em_max  \
0  55784.795689  55785.043473    344.261       344.261  0.001221  0.001231   
1  55784.795689  55785.043473    344.261       344.261  0.001212  0.001221   
2  55784.795689  55785.043473    344.261       344.261  0.001297  0.001308   
3  55784.795689  55785.043473    344.261       344.261  0.001287  0.001297   
4  55950.253573  55950.305961   1512.000      1512.000  0.001360  0.001366   

   em_res_power pol_states                                o_ucd band_list  \
0  251315.70776    /XX/YY/  phot.flux.density;phys.polarization         6   
1  253235.70776    /XX/YY/  phot.flux.density;phys.polarization         6   
2  236599.53752    /XX/YY/  phot.flux.density;phys.polarization         6   
3  238519.53752    /XX/YY/  phot.flux.density;phys.polarization         6   
4  451534.98200    /XX/YY/  phot.flux.density;phys.polarization         6   

   em_resolution                                            authors  \
0     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
1     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
2     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
3     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
4     614.023326  McCoy, Mark; Ott, Jürgen; Meier, David S.; Mul...   

                                        pub_abstract  publication_year  \
0  Centaurus A, with its gas-rich elliptical host...              2014   
1  Centaurus A, with its gas-rich elliptical host...              2014   
2  Centaurus A, with its gas-rich elliptical host...              2014   
3  Centaurus A, w

-----------------


## Example 1c: Query the ALMA source name "Centaurus"

Although in most cases, using the name resolver as above is the best way to search for source names, there can be occasions where searching for the name as given by the PI is useful. (Note that SQL queries are case-sensitive).

In [10]:
query_alma_source_name_exact(service, "Centaurus A")

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   

       proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00008.SV      Public     309.512363     19.416239   
1  2011.0.00008.SV      Public     309.512363     19.416239   
2  2011.0.00008.SV      Public     309.512363     19.416239   
3  2011.0.00008.SV      Public     309.512363     19.416239   

              obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   

                    obs_id dataproduct_type  calib_level  target_name  \
0  uid://A002/X259150/X157             cube            2  Centaurus A   
1  uid://A002/X259150/X157             cube            2  Centaurus A   
2  uid://A002/X259150/X157             cube            2  Centaurus A   
3  uid://A002/X259150/X157             cube            2  Centaurus A   

         s_ra      s_dec     s_fov  \
0  201.360719 -43.020553  0.058089   
1  201.360719 -43.020553  0.058089   
2  201.360719 -43.020553  0.058089   
3  201.360719 -43.020553  0.058089   

                                            s_region  s_resolution  \
0  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
1  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
2  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
3  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   

          t_min         t_max  t_exptime  t_resolution    em_min    em_max  \
0  55784.795689  55785.043473    344.261       344.261  0.001221  0.001231   
1  55784.795689  55785.043473    344.261       344.261  0.001212  0.001221   
2  55784.795689  55785.043473    344.261       344.261  0.001297  0.001308   
3  55784.795689  55785.043473    344.261       344.261  0.001287  0.001297   

   em_res_power pol_states                                o_ucd band_list  \
0  251315.70776    /XX/YY/  phot.flux.density;phys.polarization         6   
1  253235.70776    /XX/YY/  phot.flux.density;phys.polarization         6   
2  236599.53752    /XX/YY/  phot.flux.density;phys.polarization         6   
3  238519.53752    /XX/YY/  phot.flux.density;phys.polarization         6   

   em_resolution                                            authors  \
0     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
1     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
2     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
3     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   

                                        pub_abstract  publication_year  \
0  Centaurus A, with its gas-rich elliptical host...              2014   
1  Centaurus A, with its gas-rich elliptical host...              2014   
2  Centaurus A, with its gas-rich elliptical host...              2014   
3  Centaurus A, with its gas-rich elliptical host...              2014   

                                   proposal_abstract schedblock_name  \
0  Science Verification (SV) is the process by wh...     CenA mosaic   
1  Science Verification (SV) is the process by wh...     CenA mosaic   
2  Science Verification (SV) is the process by wh...     CenA mosaic   
3  Science Verification (SV) is the process by wh...     CenA mosaic   

  proposal_authors  sensitivity_10kms  cont_sensitivity_bandwidth       pwv  \
0                           13.319542                    0.432702  1.663192   
1                           13.283133      

-----------------

## Example 1d: Query the source name "Centaurus"
Since source names in the ALMA proposals might be spelled differently it can be useful to search for parts of the name.

In [11]:
table = query_alma_source_name_included(service, "ntaur")
table.head(5) ### showing only first 5 rows

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

       proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00008.SV      Public     309.512363     19.416239   
1  2011.0.00008.SV      Public     309.512363     19.416239   
2  2011.0.00008.SV      Public     309.512363     19.416239   
3  2011.0.00008.SV      Public     309.512363     19.416239   
4   2012.1.00019.S      Public     309.515913     19.417223   

              obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
4   ADS/JAO.ALMA#2012.1.00019.S           ALMA           JAO            ALMA   

                    obs_id dataproduct_type  calib_level  target_name  \
0  uid://A002/X259150/X157             cube            2  Centaurus A   
1  uid://A002/X259150/X157             cube            2  Centaurus A   
2  uid://A002/X259150/X157             cube            2  Centaurus A   
3  uid://A002/X259150/X157             cube            2  Centaurus A   
4   uid://A002/X6444ba/X88             cube            2  Centaurus_A   

         s_ra      s_dec     s_fov  \
0  201.360719 -43.020553  0.058089   
1  201.360719 -43.020553  0.058089   
2  201.360719 -43.020553  0.058089   
3  201.360719 -43.020553  0.058089   
4  201.365065 -43.019111  0.051984   

                                            s_region  s_resolution  \
0  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
1  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
2  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
3  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
4  Polygon ICRS 201.390398 -43.031990 201.392746 ...      4.251107   

          t_min         t_max  t_exptime  t_resolution    em_min    em_max  \
0  55784.795689  55785.043473    344.261       344.261  0.001221  0.001231   
1  55784.795689  55785.043473    344.261       344.261  0.001212  0.001221   
2  55784.795689  55785.043473    344.261       344.261  0.001297  0.001308   
3  55784.795689  55785.043473    344.261       344.261  0.001287  0.001297   
4  56658.442943  56680.464690    119.578       119.578  0.001362  0.001375   

    em_res_power pol_states                                o_ucd band_list  \
0  251315.707760    /XX/YY/  phot.flux.density;phys.polarization         6   
1  253235.707760    /XX/YY/  phot.flux.density;phys.polarization         6   
2  236599.537520    /XX/YY/  phot.flux.density;phys.polarization         6   
3  238519.537520    /XX/YY/  phot.flux.density;phys.polarization         6   
4  225399.234508    /XX/YY/  phot.flux.density;phys.polarization         6   

   em_resolution                                            authors  \
0     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
1     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
2     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
3     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
4    2456.090639                                                      

                                        pub_abstract  publication_year  \
0  Centaurus A, with its gas-rich elliptical host...              2014   
1  Centaurus A, with its gas-rich elliptical host...              2014   
2  Centaurus A, with its gas-rich elliptical host...              2014   
3  Centauru